In [98]:
import pandas as pd
import torch
from torchtext.vocab import vocab
from sklearn.model_selection import train_test_split
from tqdm.notebook import tqdm
from collections import Counter

In [99]:
dev_0_in = "./en-ner-conll-2003/dev-0/in.tsv"
test_A_in = "./en-ner-conll-2003/test-A/in.tsv"

dev_0_out = "./en-ner-conll-2003/dev-0/out.tsv"
test_A_out = "./en-ner-conll-2003/test-A/out.tsv"

train = "./en-ner-conll-2003/train/train.tsv"
expected = "./en-ner-conll-2003/dev-0/expected.tsv"

In [100]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [101]:
def load_datasets():
    train_data = pd.read_csv(
        "./en-ner-conll-2003/train/train.tsv.xz", compression="xz", sep="\t", names=["Tag", "Sentence"]
    )
    dev_data = pd.read_csv(dev_0_in, sep="\t", names=["Sentence"])
    dev_labels = pd.read_csv(expected, sep="\t", names=["Tag"])
    test_data = pd.read_csv(test_A_in, sep="\t", names=["Sentence"])

    return train_data, dev_data, dev_labels, test_data

train_data, dev_data, dev_labels, test_data = load_datasets()

train_sentences, val_sentences, train_tags, val_tags = train_test_split(
    train_data["Sentence"], train_data["Tag"], test_size=0.1, random_state=42
)

train_data = pd.DataFrame({"Sentence": train_sentences, "Tag": train_tags})
val_data = pd.DataFrame({"Sentence": val_sentences, "Tag": val_tags})

def tokenize_column(dataframe, column):
    return dataframe[column].apply(lambda x: x.split())

train_data["tokens"] = tokenize_column(train_data, "Sentence")
train_data["tag_tokens"] = tokenize_column(train_data, "Tag")
val_data["tokens"] = tokenize_column(val_data, "Sentence")
val_data["tag_tokens"] = tokenize_column(val_data, "Tag")
dev_data["tokens"] = tokenize_column(dev_data, "Sentence")
dev_labels["tag_tokens"] = tokenize_column(dev_labels, "Tag")
test_data["tokens"] = tokenize_column(test_data, "Sentence")

In [102]:
train_data.columns

Index(['Sentence', 'Tag', 'tokens', 'tag_tokens'], dtype='object')

In [103]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [104]:
def data_process(token_lists, v, device):
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in tokens] + [v["<eos>"]],
            dtype=torch.long,
            device=device,
        )
        for tokens in token_lists
    ]

In [105]:
v = build_vocab(train_data["tokens"])
v.set_default_index(v["<unk>"])

In [106]:
itos = v.get_itos()
print(itos)

['<unk>', '<pad>', '<bos>', '<eos>', 'SOCCER', '-', 'POLISH', 'FIRST', 'DIVISION', 'RESULTS', '.', '</S>', 'WARSAW', '1996-08-24', 'Results', 'of', 'Polish', 'first', 'division', 'soccer', 'matches', 'on', 'Saturday', ':', 'Amica', 'Wronki', '3', 'Hutnik', 'Krakow', '0', 'Sokol', 'Tychy', '5', 'Lech', 'Poznan', 'Rakow', 'Czestochowa', '1', 'Stomil', 'Olsztyn', '4', 'Wisla', 'Gornik', 'Zabrze', 'Slask', 'Wroclaw', 'Odra', 'Wodzislaw', 'GKS', 'Katowice', 'Polonia', 'Warsaw', 'Zaglebie', 'Lubin', '2', 'LKS', 'Lodz', 'Legia', 'Belchatow', 'CRICKET', 'POLLOCK', 'CONCLUDES', 'WARWICKSHIRE', 'CAREER', 'WITH', 'FLOURISH', 'LONDON', '1996-08-25', 'South', 'African', 'fast', 'bowler', 'Shaun', 'Pollock', 'concluded', 'his', 'Warwickshire', 'career', 'with', 'a', 'flourish', 'Sunday', 'by', 'taking', 'the', 'final', 'three', 'wickets', 'during', 'county', "'s", 'league', 'victory', 'over', 'Worcestershire', ',', 'who', 'returns', 'home', 'Tuesday', 'for', 'an', 'ankle', 'operation', 'took', 'last

In [107]:
train_tensor = data_process(train_data["tokens"], v, device)
val_tensor = data_process(val_data["tokens"], v, device)
dev_tensor = data_process(dev_data["tokens"], v, device)
test_tensor = data_process(test_data["tokens"], v, device)

In [108]:
tag_list = ["O", "B-PER", "I-PER", "B-ORG", "I-ORG", "B-LOC", "I-LOC", "B-MISC", "I-MISC"]

tag_to_index = {tag: idx for idx, tag in enumerate(tag_list)}

def convert_tags_to_tensor(tag_tokens, tag_to_index, device):
    return [
        torch.tensor(
            [0] + [tag_to_index[tag] for tag in tags] + [0],
            dtype=torch.long,
            device=device,
        )
        for tags in tag_tokens
    ]

train_tag_tensor = convert_tags_to_tensor(train_data["tag_tokens"], tag_to_index, device)
val_tag_tensor = convert_tags_to_tensor(val_data["tag_tokens"], tag_to_index, device)
dev_tag_tensor = convert_tags_to_tensor(dev_labels["tag_tokens"], tag_to_index, device)

In [109]:
tag_to_index = {tag: idx for idx, tag in enumerate(tag_list)}
max_tag_index = max(tag_to_index.values()) + 1

In [110]:
class LSTMModel(torch.nn.Module):
    def __init__(self, vocab_size, embed_size, hidden_size, num_layers, output_size):
        super(LSTMModel, self).__init__()
        self.embedding = torch.nn.Embedding(vocab_size, embed_size)
        self.lstm = torch.nn.LSTM(embed_size, hidden_size, num_layers, batch_first=True)
        self.fc = torch.nn.Linear(hidden_size, output_size)

    def forward(self, x):
        embedded = torch.relu(self.embedding(x))
        lstm_out, _ = self.lstm(embedded)
        logits = self.fc(lstm_out)
        return logits


In [111]:
model = LSTMModel(len(itos), 100, 100, 1, max_tag_index).to(device)
loss_fn = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters())

In [112]:
def eval_model(dataset_tokens, dataset_labels, model, tag_to_index):
    Y_true = []
    Y_pred = []
    
    index_to_tag = {v: k for k, v in tag_to_index.items()}

    for i in range(len(dataset_labels)):
        inputs = dataset_tokens[i].unsqueeze(0).to('cuda')
        true_labels = dataset_labels[i].cpu().numpy() 
        
        with torch.no_grad():
            logits = model(inputs).squeeze(0)
            predicted = torch.argmax(logits, dim=1)
            predicted_labels = predicted.cpu().numpy()

        true_tags = [index_to_tag[label] for label in true_labels[1:-1]]
        pred_tags = [index_to_tag[label] for label in predicted_labels[1:-1]]

        if len(true_tags) == len(pred_tags):
            Y_true.extend(true_tags)
            Y_pred.extend(pred_tags)
        else:
            continue

    return Y_true, Y_pred

In [113]:
def calculate_accuracy(true_labels, pred_labels):
    correct = sum(t == p for t, p in zip(true_labels, pred_labels))
    total = len(true_labels)
    accuracy = correct / total if total > 0 else 0
    return accuracy

In [114]:
epochs = 10

for epoch in range(epochs):
    model.train()
    
    for i in range(len(train_tag_tensor)):
        inputs = train_tensor[i].unsqueeze(0).to('cuda')
        targets = train_tag_tensor[i].unsqueeze(1).to('cuda')

        optimizer.zero_grad()
        outputs = model(inputs)
        loss = loss_fn(outputs.squeeze(0), targets.squeeze(1))
        loss.backward()
        optimizer.step()

    model.eval()

    val_tensor_cuda = [tensor.to('cuda') for tensor in val_tensor]
    val_tag_tensor_cuda = [tensor.to('cuda') for tensor in val_tag_tensor]

    Y_true, Y_pred = eval_model(val_tensor_cuda, val_tag_tensor_cuda, model, tag_to_index)
    accuracy = calculate_accuracy(Y_true, Y_pred)
    print(f"Epoka {epoch + 1}, Dokładność: {accuracy * 100:.2f}")
    


Epoka 1, Dokładność: 85.41
Epoka 2, Dokładność: 88.92
Epoka 3, Dokładność: 90.99
Epoka 4, Dokładność: 92.06
Epoka 5, Dokładność: 92.69
Epoka 6, Dokładność: 93.19
Epoka 7, Dokładność: 93.50
Epoka 8, Dokładność: 93.78
Epoka 9, Dokładność: 93.94
Epoka 10, Dokładność: 94.08


In [115]:
def predict_labels(tokens, model, tag_to_index):
    predictions = []
    index_to_tag = {v: k for k, v in tag_to_index.items()}

    for i in range(len(tokens)):
        inputs = tokens[i].unsqueeze(0)
        with torch.no_grad():
            logits = model(inputs).squeeze(0)
            predicted = torch.argmax(logits, dim=1)
            tags = [index_to_tag[label.item()] for label in predicted[1:-1]]
            predictions.append(" ".join(tags))

    return predictions

In [116]:
val_tensor_cuda = [tensor.to('cuda') for tensor in val_tensor]
val_tag_tensor_cuda = [tensor.to('cuda') for tensor in val_tag_tensor] 

Y_true, Y_pred = eval_model(val_tensor_cuda, val_tag_tensor_cuda, model, tag_to_index)
accuracy = calculate_accuracy(Y_true, Y_pred)
print(f"Dokładność: {accuracy * 100:.2f}%")

Dokładność: 94.08%


In [117]:
dev_predictions = predict_labels(dev_tensor, model, tag_to_index)
dev_predictions_df = pd.DataFrame(dev_predictions, columns=["Tag"])
dev_predictions_df.to_csv(dev_0_out, index=False, header=False)

test_predictions = predict_labels(test_tensor, model, tag_to_index)
test_predictions_df = pd.DataFrame(test_predictions, columns=["Tag"])
test_predictions_df.to_csv(test_A_out, index=False, header=False)

In [118]:
dev_predictions_df.head(10)

Tag
0  O O O O O O O O O O O O B-LOC O O B-LOC I-LOC ...
1  O O B-MISC B-MISC I-MISC O O O B-LOC O O O O O...
2  O O O O O O O B-LOC O O B-LOC O O O O O O O O ...
3  O O O O O B-LOC O O O B-LOC O O O O O O O B-MI...
4  O O O O O O O B-LOC O O O O O O O O O O O O O ...
5  O O B-ORG O O O O O O O B-LOC O O B-LOC O B-LO...
6  O O O O O O O O O O O B-LOC O O O O O O O O O ...
7  O O O O O O O O O O O O O O B-LOC O O O O O B-...
8  O O B-MISC I-MISC I-MISC O O O O B-LOC I-LOC O...
9  O O O O B-MISC I-MISC O O O O B-LOC O O O O B-...

In [119]:
test_predictions_df.head(10)

Tag
0  O O O O O O O B-ORG O O O O O O O O O O B-LOC ...
1  B-ORG I-ORG O O O O O O O O O O B-LOC O O B-LO...
2  O O O O O O O O O O O O O B-LOC I-ORG I-LOC O ...
3  O O B-MISC O O O O O O B-LOC O O O O O B-MISC ...
4  O O O B-MISC O O O O O O O B-LOC I-ORG I-LOC O...
5  O O B-LOC O B-LOC I-LOC O O O O O O O B-MISC O...
6  O O B-MISC O I-MISC O O O O O B-LOC O O O O O ...
7  O O O B-ORG O O O B-LOC O O B-MISC O O O O O O...
8  O O B-LOC O O O O O O O O O O B-LOC O O B-ORG ...
9  O O O O O O B-LOC O O O O O O O O O O O O O O ...